In [1]:
import os
import sys

import pickle

import pandas as pd
import numpy as np
import datetime
from dateutil.relativedelta import relativedelta
import sklearn.preprocessing as skp

import scipy.stats as scs
import statsmodels.stats as sms

import matplotlib.pyplot as plt
import matplotlib as mpl
%matplotlib inline

import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
from plotly import tools
py.init_notebook_mode(connected=True)

In [2]:
from sklearn.linear_model import LogisticRegression

In [3]:
from TCC_pkg import dataanalysis as da
from TCC_pkg import testspecification as tspec
from TCC_pkg import autoregressive as ar

/opt/anaconda3/envs/crypto-env/lib/python3.6/site-packages/statsmodels/compat/pandas.py:56: FutureWarning:

The pandas.core.datetools module is deprecated and will be removed in a future version. Please use the pandas.tseries module instead.



# <span style='color:crimson'>1.</span> Input Data

## <span style='color:MediumBlue'>1.1.</span> Stock series

In [4]:
series_name = 'aapl'
with open('../Data/{}.pkl'.format(series_name), 'rb') as f:
    df_raw = pickle.load(f)
    
df_raw

Close        High         Low        Open       Volume  \
Date                                                                      
2011-01-03   42.354338   42.443013   41.746018   41.849279  111284600.0   
2011-01-04   42.575382   42.730884   42.171849   42.723173   77270200.0   
2011-01-05   42.923655   42.967350   42.345342   42.351768   63879900.0   
2011-01-06   42.888956   43.084298   42.782290   43.016108   75107200.0   
2011-01-07   43.196105   43.225663   42.653776   42.922370   77982800.0   
2011-01-10   44.010241   44.109839   43.331044   43.544377  112140000.0   
2011-01-11   43.905502   44.332168   43.626626   44.321887  111027000.0   
2011-01-12   44.262770   44.264056   43.951767   44.112409   75647600.0   
2011-01-13   44.424698   44.548071   44.189517   44.357871   74195100.0   
2011-01-14   44.784537   44.784537   44.265341   44.451686   77210000.0   
2011-01-18   43.778273   44.306786   41.895544   42.347913  470249500.0   
2011-01-19   43.545663   44.799959   43.293775   44.767830  283903200.0   
2011-01-20   42.754017   43.476265   42.425021   43.235944  191197300.0   
2011-01-21   41.988074   43.036747   41.976507   42.894097  188600300.0   
2011-01-24   43.367028   43.367028   41.988074   42.007351  143670800.0   
2011-01-25   43.874658   43.879799   42.996908   43.223093  136717000.0   
2011-01-26   44.189517   44.414417   43.887510   44.075140  126718900.0   
2011-01-27   44.107269   44.297829   44.058562   44.180521   71256500.0   
2011-01-28   43.193534   44.260200   42.862997   44.230642  148014300.0   
2011-01-31   43.607349   43.699879   42.962209   43.154980   94311700.0   
2011-02-01   44.341164   44.420843   43.820682   43.861807  106658300.0   
2011-02-02   44.249919   44.369437   44.150963   44.266626   64738800.0   
2011-02-03   44.136827   44.239638   43.508394   44.183092   98449400.0   
2011-02-04   44.530079   44.555782   44.145823   44.162530   80460100.0   
2011-02-07   45.221484   45.397548   44.676585   44.708714  121255400.0   
2011-02-08   45.648151   45.689275   45.256183   45.452809   95260200.0   
2011-02-09   46.028552   46.136504   45.605741   45.646866  120686300.0   
2011-02-10   45.563331   46.265018   44.722850   45.929596  232137500.0   
2011-02-11   45.860199   45.982287   45.434830   45.590654   91893200.0   
2011-02-14   46.159636   46.198190   45.842207   45.852488   77604100.0   
...                ...         ...         ...         ...          ...   
2018-02-13  164.340000  164.750000  161.650000  161.950000   32104756.0   
2018-02-14  167.370000  167.540000  162.880000  163.045000   39669178.0   
2018-02-15  172.990000  173.090000  169.000000  169.790000   50609595.0   
2018-02-16  172.430000  174.820000  171.770000  172.360000   39638793.0   
2018-02-20  171.850000  174.260000  171.420000  172.050000   33531012.0   
2018-02-21  171.070000  174.120000  171.010000  172.830000   35833514.0   
2018-02-22  172.600000  173.950000  171.710000  171.800000   30504116.0   
2018-02-23  175.555000  175.650000  173.540000  173.670000   33329232.0   
2018-02-26  178.970000  179.390000  176.210000  176.350000   36886432.0   
2018-02-27  178.390000  180.480000  178.160000  179.100000   38685165.0   
2018-02-28  178.120000  180.615000  178.050000  179.260000   33604574.0   
2018-03-01  175.000000  179.775000  172.660000  178.540000   48801970.0   
2018-03-02  176.210000  176.300000  172.450000  172.800000   38453950.0   
2018-03-05  176.820000  177.740000  174.520000  175.210000   28401366.0   
2018-03-06  176.670000  178.250000  176.130000  177.910000   23788506.0   
2018-03-07  175.030000  175.850000  174.270000  174.940000   31703462.0   
2018-03-08  176.940000  177.120000  175.070000  175.480000   23163767.0   
2018-03-09  179.980000  180.000000  177.390000  177.960000   31385134.0   
2018-03-12  181.720000  182.390000  180.210000  180.290000   32055405.0   
2018-03-13  179.970000  183.500000  179.240000  182.590000   31168404.0   
2018-03-14  178.440000  180.520000  177.81

In [5]:
da.candleplot(df_raw.drop(columns=['Direction', 'Volume']))

## <span style='color:MediumBlue'>1.2.</span> Network Data

## <span style='color:MediumBlue'>1.3.</span> Sentiment Analysis

## <span style='color:MediumBlue'>1.4.</span> News and Online Data

# <span style='color:crimson'>2.</span> Data Cleaning

## <span style='color:MediumBlue'>2.1.</span> Data Overview

In [6]:
df = df_raw.copy()
print('Shape: {}\n'.format(df.shape))
print('Indices: \n{}\n{}\n'.format(df.index[:5], df.index[-5:]))
print('Columns: \n{}\n'.format(df.columns))
print('Describe(): \n{}\n'.format(df.describe()))

Shape: (1818, 6)

Indices: 
DatetimeIndex(['2011-01-03', '2011-01-04', '2011-01-05', '2011-01-06',
               '2011-01-07'],
              dtype='datetime64[ns]', name='Date', freq=None)
DatetimeIndex(['2018-03-21', '2018-03-22', '2018-03-23', '2018-03-26',
               '2018-03-27'],
              dtype='datetime64[ns]', name='Date', freq=None)

Columns: 
Index(['Close', 'High', 'Low', 'Open', 'Volume', 'Direction'], dtype='object')

Describe(): 
             Close         High          Low         Open        Volume  \
count  1818.000000  1818.000000  1818.000000  1818.000000  1.818000e+03   
mean     93.590007    94.390432    92.756979    93.598986  7.538906e+07   
std      36.015008    36.231882    35.780549    36.004098  5.385936e+07   
min      40.523015    40.828878    39.903578    40.697794  1.147592e+07   
25%      65.139696    65.892813    64.477108    65.238411  3.497941e+07   
50%      90.851617    91.566725    89.977604    90.887746  6.085693e+07   
75%     114.83002

## <span style='color:MediumBlue'>2.2.</span> Data Cleaning

In [7]:
# Adjust time-series
df = df_raw.copy()

# 1. Find zeros or negative values
print('Number of zero-values: {}'.format(df[df==0].count().values))

# 2. Find NaNs
print('Number of NaNs: {}'.format(df[df.isna().values].count().values))

# 3. Eliminate entries with NaNs
df = df.dropna(how='any', axis=0)

# 4. Gaps
date_gaps = np.array([(df.index[i]-df.index[i-1]).days for i in range(1,len(df.index))])
print('Average gap: {}'.format(date_gaps.mean()))
print('Max gap: {}'.format(date_gaps.max()))
print('No. of gaps greater than 5: {}'.format(len(date_gaps[date_gaps>5])))
print('15 greatest gaps: {}'.format(np.sort(date_gaps)[-15:]))
print('Dates of greatest gap: \n{}\n'.format(df.iloc[date_gaps.argmax()-1:date_gaps.argmax()+3]))

df_adj = df

Number of zero-values: [0 0 0 0 0 0]
Number of NaNs: [1 1 1 1 1 0]
Average gap: 1.453193832599119
Max gap: 5
No. of gaps greater than 5: 0
15 greatest gaps: [4 4 4 4 4 4 4 4 4 4 4 4 4 4 5]
Dates of greatest gap: 
                Close       High        Low       Open       Volume  Direction
Date                                                                          
2012-10-25  78.668550  80.276928  78.153848  80.018803  164081400.0       -1.0
2012-10-26  77.953801  79.244427  76.275988  78.654611  254608200.0       -1.0
2012-10-31  76.833538  77.690514  75.850081  76.776751  127500800.0       -1.0
2012-11-01  76.990982  77.824739  76.685116  77.207820   90324500.0        1.0



## <span style='color:MediumBlue'>2.3.</span> Outliers

In [8]:
df = df_adj.copy()
ts = df_adj['Close']
n_std = 3

df = pd.concat([df, da.roll_stats(ts=ts, window=30)], axis=1).dropna(how='any',axis=0)
df['Upper'] = df['Rolling Mean'] + n_std*df['Rolling Variance'].apply(np.sqrt)
df['Lower'] = df['Rolling Mean'] - n_std*df['Rolling Variance'].apply(np.sqrt)

da.plotscatter(df.drop(columns='Direction'))

# Outlier criterion
df_out = df[(df['Close'] > df['Upper']) | (df['Close'] < df['Lower'])]
df['Out'] = df.loc[df_out.index, 'Close']

df = df.replace(np.nan, 0) # for plotting
da.plotscatter(df.drop(columns='Direction'))

df = df.drop(df_out.index)
df_adj_noout = df[['Close']]

# <span style='color:crimson'>*.</span> Input-Output Definition

In [9]:
df = df_adj.copy()

input_cols = ['Close','High','Low','Open','Volume']
target_col = ['Direction']

# The last index does not correspond to a sample because there is no information about the next day's direction
X_raw, y_raw = df.loc[df.index[:-1],input_cols], df[target_col].shift(-1).loc[df.index[:-1]]

# <span style='color:crimson'>3.</span> Data Generation

**Good references: [1,6,33,35,39]**

## <span style='color:MediumBlue'>3.1.</span> Technical Indicators

In [10]:
X = X_raw.copy()
X.describe()

Close         High          Low         Open        Volume
count  1816.000000  1816.000000  1816.000000  1816.000000  1.816000e+03
mean     93.577059    94.374566    92.744230    93.583385  7.538936e+07
std      35.972003    36.181699    35.737853    35.954339  5.387565e+07
min      40.523015    40.828878    39.903578    40.697794  1.147592e+07
25%      65.170090    65.959239    64.501700    65.344658  3.493944e+07
50%      90.851617    91.566725    89.977604    90.887746  6.085693e+07
75%     114.782767   115.398129   113.848545   114.735599  9.965060e+07
max     181.720000   183.500000   180.210000   182.590000  4.702495e+08

## <span style='color:MediumBlue'>3.*.</span> Final Features

In [11]:
X = X_raw.copy()
y = y_raw.copy()

# Test #1: LAGGED VALS
n_lags = 3
X.shift(1)

X_feat = pd.DataFrame(data=[], index=X_raw.index, columns=[]) # empty dataframe
for lag in range(0,n_lags):
    col_names = {col:col+'(t-%d)'%lag for col in X.columns}
    X_tmp = X.shift(periods=lag)
    X_tmp = X_tmp.rename(columns=col_names)
    X_feat = pd.concat([X_feat, X_tmp], axis=1)
    
X_feat = X_feat.dropna()
y_feat = y.loc[X_feat.index]

y_feat

Direction
Date                 
2011-01-06        1.0
2011-01-07        1.0
2011-01-10       -1.0
2011-01-11        1.0
2011-01-12        1.0
2011-01-13        1.0
2011-01-14       -1.0
2011-01-18       -1.0
2011-01-19       -1.0
2011-01-20       -1.0
2011-01-21        1.0
2011-01-24        1.0
2011-01-25        1.0
2011-01-26       -1.0
2011-01-27       -1.0
2011-01-28        1.0
2011-01-31        1.0
2011-02-01       -1.0
2011-02-02       -1.0
2011-02-03        1.0
2011-02-04        1.0
2011-02-07        1.0
2011-02-08        1.0
2011-02-09       -1.0
2011-02-10        1.0
2011-02-11        1.0
2011-02-14        1.0
2011-02-15        1.0
2011-02-16       -1.0
2011-02-17       -1.0
...               ...
2018-02-12        1.0
2018-02-13        1.0
2018-02-14        1.0
2018-02-15       -1.0
2018-02-16       -1.0
2018-02-20       -1.0
2018-02-21        1.0
2018-02-22        1.0
2018-02-23        1.0
2018-02-26       -1.0
2018-02-27       -1.0
2018-02-28       -1.0
2018-03-01        1.0
2018-03-02        1.0
2018-03-05       -1.0
2018-03-06       -1.0
2018-03-07        1.0
2018-03-08        1.0
2018-03-09        1.0
2018-03-12       -1.0
2018-03-13       -1.0
2018-03-14        1.0
2018-03-15       -1.0
2018-03-16       -1.0
2018-03-19       -1.0
2018-03-20       -1.0
2018-03-21       -1.0
2018-03-22       -1.0
2018-03-23        1.0
2018-03-26       -1.0

[1814 rows x 1 columns]

# <span style='color:crimson'>4.</span> Data Transformation

## <span style='color:MediumBlue'>4.1.</span> Scaling/Normalization

Fonte: http://scikit-learn.org/stable/modules/preprocessing.html

In [12]:
# Isso tem que virar uma funcao
def scale_train_test_sets(X_train, X_test):
    # Define scaler
    scaler = skp.MinMaxScaler(feature_range=(-1,1))

    # COLUMN-WISE transformation, i.e., transform each feature independently
    X_train_scaled = pd.DataFrame(scaler.fit_transform(X_train), index=X_train.index, columns=X_train.columns) 

    # Apply same scaling parameters to test set (during test we do not know future values to scale)
    X_test_scaled = pd.DataFrame(scaler.transform(X_test), index=X_test.index, columns=X_test.columns)

    return X_train_scaled, X_test_scaled

# <span style='color:crimson'>5.</span> Feature Selection

## <span style='color:MediumBlue'>5.1.</span> Correlation

## <span style='color:MediumBlue'>5.2.</span> Mutual Information

## <span style='color:MediumBlue'>5.3.</span> Regularization

### <span style='color:Goldenrod'>5.3.1.</span> Lasso

### <span style='color:Goldenrod'>5.3.2.</span> Ridge

### <span style='color:Goldenrod'>5.3.3.</span> Elastic Net

## <span style='color:MediumBlue'>5.4.</span> Feature Importance

# <span style='color:crimson'>6.</span> Feature Extraction

## <span style='color:MediumBlue'>6.1.</span> PCA

## <span style='color:MediumBlue'>6.2.</span> AE

# <span style='color:crimson'>7.</span> Test Design

In [13]:
y = y_feat

margin = 5
test_spec = tspec.TestSpec(indices=y.index, 
                            start_dates=['2017-01'], 
                            window_size=400,
                            margin=margin
                           )


# <span style='color:crimson'>*.</span> Train-test split

# <span style='color:crimson'>8.</span> Comparison Metrics

In [17]:
# BOA IMAGEM PRA EXEMPLIFICAR A IMPORTANCIA DE DIFERENCIAR/USAR INDICADORES RELATIVOS
instance = test_spec.instance[0]
X_train, X_test = X.loc[instance.train_set], X.loc[instance.test_set]
X_train, X_test = scale_train_test_sets(X_train, X_test)
da.plotscatter(X_train)
da.plotscatter(X_test)

# <span style='color:crimson'>9.</span> Models

## <span style='color:MediumBlue'>9.1.</span> Logistic Regression

Fontes:
- http://scikit-learn.org/stable/modules/linear_model.html
- http://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html

**HYPERPARAMETERS**:
- `penalty` : str, `‘l1’` or `‘l2’`, default: ‘l2’
- `C` : float, default: `1.0` - 
    - Inverse of regularization strength; must be a positive float; smaller values = stronger regularization.
        - Small C: probability curves will look more like straight lines (long transition between 0-1)
        - Large C: probability curves will look more like step function (fast transition between 0-1)

In [14]:
# Consider 5 options 
# Hyperparameters
model_func = LogisticRegression
regularizers = ['l1','l2']
reg_coeff = [0.01, 0.033, 0.66, 0.1, 0.33, 0.66, 1, 3.33, 10]
kwparams_list = list({'penalty':reg, 'C':C} for C in reg_coeff for reg in regularizers) 

import warnings
warnings.filterwarnings(action='ignore')

# Observation:
# X = (samples/examples x features/inputs) = (m x n)
X = X_feat.copy()
y = y_feat.copy()

# Define test instance
instance = test_spec.instance[0]

# Define test set
X_test = instance.test_set

# Cross-validation
best_perf = 0
for kwparams in kwparams_list:
    print(kwparams)
    kwparams_perf = 0
    for fold in range(instance.CrossValidation.n_folds):
        # Get cross-validation sets
        train_ind = instance.expanding_window_cv.train_sets[fold]
        val_ind = instance.expanding_window_cv.val_sets[fold]
        X_train, X_val = X.loc[train_ind], X.loc[val_ind]
        y_train, y_val = y.loc[train_ind], y.loc[val_ind]

        assert all(X_train.index == y_train.index) and all(X_val.index == y_val.index)
        
        # Scale values
        X_train, X_val = scale_train_test_sets(X_train, X_val)
        y_train, y_val = y_train.values.ravel(), y_val.values.ravel() # transforms into array (m,)

        # Fit logistic regression model
        log_reg = LogisticRegression(**kwparams)
        log_reg.fit(X_train, y_train)

        y_pred = log_reg.predict(X_val)
        y_pred_prob = log_reg.predict_proba(X_val) # use for AUC-ROC

        # pd.DataFrame(data=da.classification_metrics(y_true=y_test, y_pred=y_pred), columns=['LR'])
        fold_perf = da.classification_metrics(y_true=y_val, y_pred=y_pred)
        kwparams_perf += fold_perf['5. Accuracy']
        
    if kwparams_perf > best_perf:
        best_perf = kwparams_perf
        best_params = kwparams
        
# Train on entire train set
X_train, X_test = X.loc[instance.train_set], X.loc[instance.test_set]
y_train, y_test = y.loc[instance.train_set], y.loc[instance.test_set]

# Scale values
X_train, X_test = scale_train_test_sets(X_train, X_test)
y_train, y_test = y_train.values.ravel(), y_test.values.ravel() # transforms into array (m,)

log_reg = LogisticRegression(**best_params)
log_reg.fit(X_train, y_train)

y_pred = log_reg.predict(X_test)
y_pred_prob = log_reg.predict_proba(X_test) # use for AUC-ROC

# Test performance
ml_res = {}
ml_res['LR'] = da.classification_metrics(y_true=y_test, y_pred=y_pred)
test_perf = pd.DataFrame(data=ml_res)                                     

{'penalty': 'l1', 'C': 0.01}
{'penalty': 'l2', 'C': 0.01}
{'penalty': 'l1', 'C': 0.033}
{'penalty': 'l2', 'C': 0.033}
{'penalty': 'l1', 'C': 0.66}
{'penalty': 'l2', 'C': 0.66}
{'penalty': 'l1', 'C': 0.1}
{'penalty': 'l2', 'C': 0.1}
{'penalty': 'l1', 'C': 0.33}
{'penalty': 'l2', 'C': 0.33}
{'penalty': 'l1', 'C': 0.66}
{'penalty': 'l2', 'C': 0.66}
{'penalty': 'l1', 'C': 1}
{'penalty': 'l2', 'C': 1}
{'penalty': 'l1', 'C': 3.33}
{'penalty': 'l2', 'C': 3.33}
{'penalty': 'l1', 'C': 10}
{'penalty': 'l2', 'C': 10}


In [15]:
test_perf

LR
1. Mathews_CorrCoef    0.000000
2. F-beta_0.5          0.000000
3. F1                  0.000000
4. Cohen_Kappa         0.000000
5. Accuracy            0.469055
5. Precision           0.000000
5. Recall              0.000000
FN                   163.000000
FP                     0.000000
TN                   144.000000
TP                     0.000000

# <span style='color:crimson'>10.</span> Tests

# <span style='color:crimson'>11.</span> Results

# <span style='color:crimson'>12.</span> Comparisons